## Installing Haystack

To start, let's install the latest release of Haystack with `pip`:

In [1]:
# %%bash

# pip install --upgrade pip
# pip install farm-haystack[colab]

Set the logging level to INFO:

In [1]:
import logging

logging.basicConfig(format="%(levelname)s - %(name)s -  %(message)s", level=logging.WARNING)
logging.getLogger("haystack").setLevel(logging.INFO)

## Initializing the ElasticsearchDocumentStore


1. Download, extract, and set the permissions for the Elasticsearch installation image:

In [2]:
import elasticsearch

In [ ]:
%%bash

wget https://artifacts.elastic.co/downloads/elasticsearch/elasticsearch-7.9.2-linux-x86_64.tar.gz -q
tar -xzf elasticsearch-7.9.2-linux-x86_64.tar.gz
chown -R daemon:daemon elasticsearch-7.9.2

2. Start the server:

In [5]:
%%bash --bg

sudo -u daemon -- elasticsearch-7.9.2/bin/elasticsearch

In [3]:
import time
time.sleep(30)

4. Initialize the ElasticsearchDocumentStore:


In [4]:
from haystack.utils import launch_es
launch_es()

In [5]:
import os
from haystack.document_stores import ElasticsearchDocumentStore

# Get the host where Elasticsearch is running, default to localhost
host = os.environ.get("ELASTICSEARCH_HOST", "localhost")

document_store = ElasticsearchDocumentStore(
    host=host,
    username="",
    password="",
    index="document"
)

/opt/conda/envs/pytorch/lib/python3.9/site-packages/elasticsearch/connection/base.py:200: ElasticsearchWarning: Elasticsearch built-in security features are not enabled. Without authentication, your cluster could be accessible to anyone. See https://www.elastic.co/guide/en/elasticsearch/reference/7.17/security-minimal-setup.html to enable security.
  warnings.warn(message, category=ElasticsearchWarning)


## Indexing Documents with a Pipeline


In [6]:
import pandas as pd
import re

df = pd.read_csv("pt_question_answers.csv")

df.shape

df[["pt_title", "pt_body", "pt_answer"]]

df["text"] = "question: " + df["pt_title"] + "\n" + df["pt_body"] + "\n" + "answer: " + df["pt_answer"]
# df["text"] = "question: " + df["pt_title"] + "\n" + "answer: " + df["pt_answer"]

df = df[["text"]]

CLEANR = re.compile('<.*?>') 

def cleanhtml(raw_html):
  cleantext = re.sub(CLEANR, '', raw_html)
  return cleantext

df["text"] = df["text"].apply(lambda x: cleanhtml(x))

df["text"] = df["text"].str.lower()

df

text
0      question: extracting the top-k value-indices from a 1-d tensor\nanswer: as o...
1      question: how to display custom images in tensorboard (e.g. matplotlib plots...
2      question: python wheels: cp27mu not supported\nanswer: yes, that is possible...
3      question: loading torch7 trained models (.t7) in pytorch\nanswer: view() res...
4      question: pytorch: how to use dataloaders for custom datasets\nanswer: while...
...                                                                                ...
14588  question: how to disable neptune callback in transformers trainer runs?\nans...
14589  question: bgr to rgb for cub_200 images by image.split()\nanswer: i would st...
14590  question: neural networks extending learning domain\nanswer: what you want i...
14591  question: how do i multiply tensors like this?\nanswer: you should familiari...
14592  question: how do i multiply tensors like this?\nanswer: it seems like what y...

[14593 rows x 1 columns]

In [7]:
d=df['text'].tolist()
file = open('data_qa.txt','w')
file.writelines(d)
file.close()


2. Initialize the pipeline, TextConverter, and PreProcessor:

In [8]:
from haystack import Pipeline
from haystack.nodes import TextConverter, PreProcessor

indexing_pipeline = Pipeline()
text_converter = TextConverter()
preprocessor = PreProcessor(
    clean_whitespace=True,
    clean_header_footer=True,
    clean_empty_lines=True,
    split_by="word",
    split_length=1024,
    split_overlap=20,
    split_respect_sentence_boundary=True,
)


In [9]:
import os

indexing_pipeline.add_node(component=text_converter, name="TextConverter", inputs=["File"])
indexing_pipeline.add_node(component=preprocessor, name="PreProcessor", inputs=["TextConverter"])
indexing_pipeline.add_node(component=document_store, name="DocumentStore", inputs=["PreProcessor"])


3. Run the indexing pipeline to write the text data into the DocumentStore:

In [10]:
files_to_index = ['data_qa.txt']
indexing_pipeline.run_batch(file_paths=files_to_index)

INFO - haystack.pipelines.base -  It seems that an indexing Pipeline is run, so using the nodes' run method instead of run_batch.


Converting files:   0%|          | 0/1 [00:00<?, ?it/s]

Preprocessing:   0%|          | 0/1 [00:00<?, ?docs/s]

WARNING - haystack.nodes.preprocessor.preprocessor -  We found one or more sentences whose word count is higher than the split length.
WARNING - haystack.nodes.preprocessor.preprocessor -  Document 91a40bfbf38e7dc763b94c5b3d9ae101 is 10188 characters long after preprocessing, where the maximum length should be 10000. Something might be wrong with the splitting, check the document affected to prevent issues at query time.
WARNING - haystack.nodes.preprocessor.preprocessor -  Document 9b1c0974d762a8fa9ddf0d3922768b4a is 11400 characters long after preprocessing, where the maximum length should be 10000. Something might be wrong with the splitting, check the document affected to prevent issues at query time.
WARNING - haystack.nodes.preprocessor.preprocessor -  Document 30d4805eab1c5f164e26f3f3f2304bd8 is 11326 characters long after preprocessing, where the maximum length should be 10000. Something might be wrong with the splitting, check the document affected to prevent issues at query t

{'documents': [<Document: {'content': 'question: extracting the top-k value-indices from a 1-d tensor\nanswer: as of pull request #496 torch now includes a built-in api named torch.topk. example:\n\n&gt; t = torch.tensor{9, 1, 8, 2, 7, 3, 6, 4, 5}\n\n-- obtain the 3 smallest elements\n&gt; res = t:topk(3)\n&gt; print(res)\n1\n2\n3\n[torch.doubletensor of size 3]\n\n-- you can also get the indices in addition\n&gt; res, ind = t:topk(3)\n&gt; print(ind)\n2\n4\n6\n[torch.longtensor of size 3]\n\n-- alternatively you can obtain the k largest elements as follow\n-- (see the api documentation for more details)\n&gt; res = t:topk(3, true)\n&gt; print(res)\n9\n8\n7\n[torch.doubletensor of size 3]\n\nat the time of writing the cpu implementation follows a sort and narrow approach (there are plans to improve it in the future). that being said an optimized gpu implementation for cutorch is currently being reviewed.\nquestion: how to display custom images in tensorboard (e.g. matplotlib plots)?\na

## Initializing the Retriever


## BM25Retriever and FarmReader roberta

In [11]:
from haystack.nodes import BM25Retriever, EmbeddingRetriever
from haystack.nodes import FARMReaderrom haystack.nodes import FARMReader, TransformersReader
from haystack import Pipeline


bm_retriever = BM25Retriever(document_store=document_store)

In [12]:
farm_reader_roberta = FARMReader(model_name_or_path="deepset/roberta-base-squad2", use_gpu=True)

INFO - haystack.modeling.utils -  Using devices: CUDA:0 - Number of GPUs: 1
INFO - haystack.modeling.utils -  Using devices: CUDA:0 - Number of GPUs: 1
INFO - haystack.modeling.model.language_model -   * LOADING MODEL: 'deepset/roberta-base-squad2' (Roberta)
INFO - haystack.modeling.model.language_model -  Auto-detected model language: english
INFO - haystack.modeling.model.language_model -  Loaded 'deepset/roberta-base-squad2' (Roberta model) from model hub.
INFO - haystack.modeling.utils -  Using devices: CUDA:0 - Number of GPUs: 1


In [13]:
## Creating the Retriever-Reader Pipeline

bm25_querying_pipeline = Pipeline()
bm25_querying_pipeline.add_node(component=bm_retriever, name="Retriever", inputs=["Query"])
bm25_querying_pipeline.add_node(component=farm_reader_roberta, name="Reader", inputs=["Retriever"])


## EmbeddingRetriever using sentence-transformers and FarmReader albert xxlargev1

In [14]:
embedding_retriever = EmbeddingRetriever(document_store=document_store,
                              embedding_model="sentence-transformers/multi-qa-mpnet-base-dot-v1",
                               model_format="sentence_transformers")

INFO - haystack.modeling.utils -  Using devices: CUDA:0 - Number of GPUs: 1
INFO - haystack.nodes.retriever.dense -  Init retriever using embeddings of model sentence-transformers/multi-qa-mpnet-base-dot-v1


In [15]:
farm_reader_albert = FARMReader(model_name_or_path="ahotrod/albert_xxlargev1_squad2_512", use_gpu=True)

INFO - haystack.modeling.utils -  Using devices: CUDA:0 - Number of GPUs: 1
INFO - haystack.modeling.utils -  Using devices: CUDA:0 - Number of GPUs: 1
INFO - haystack.modeling.model.language_model -   * LOADING MODEL: 'ahotrod/albert_xxlargev1_squad2_512' (Albert)
INFO - haystack.modeling.model.language_model -  Auto-detected model language: english
INFO - haystack.modeling.model.language_model -  Loaded 'ahotrod/albert_xxlargev1_squad2_512' (Albert model) from model hub.
INFO - haystack.modeling.utils -  Using devices: CUDA:0 - Number of GPUs: 1


In [16]:
embedding_querying_pipeline = Pipeline()
embedding_querying_pipeline.add_node(component=embedding_retriever, name="Retriever", inputs=["Query"])
embedding_querying_pipeline.add_node(component=farm_reader_albert, name="Reader", inputs=["Retriever"])


## EmbeddingRetriever using sentence-transformers and FarmReader albert xxlargev2

In [17]:
farm_reader_albertv2 = FARMReader(model_name_or_path="mfeb/albert-xxlarge-v2-squad2", use_gpu=True)
## Creating the Retriever-Reader Pipeline

embedding_querying_pipeline1 = Pipeline()
embedding_querying_pipeline1.add_node(component=embedding_retriever, name="Retriever", inputs=["Query"])
embedding_querying_pipeline1.add_node(component=farm_reader_albertv2, name="Reader", inputs=["Retriever"])


INFO - haystack.modeling.utils -  Using devices: CUDA:0 - Number of GPUs: 1
INFO - haystack.modeling.utils -  Using devices: CUDA:0 - Number of GPUs: 1
INFO - haystack.modeling.model.language_model -   * LOADING MODEL: 'mfeb/albert-xxlarge-v2-squad2' (Albert)
INFO - haystack.modeling.model.language_model -  Auto-detected model language: english
INFO - haystack.modeling.model.language_model -  Loaded 'mfeb/albert-xxlarge-v2-squad2' (Albert model) from model hub.
INFO - haystack.modeling.utils -  Using devices: CUDA:0 - Number of GPUs: 1


## EmbeddingRetriever using sentence-transformers and TransformersReader albert xxlargev2

In [18]:
transformers_reader_albertv2 = TransformersReader(model_name_or_path="mfeb/albert-xxlarge-v2-squad2", use_gpu=True)
## Creating the Retriever-Reader Pipeline

embedding_querying_pipeline2 = Pipeline()
embedding_querying_pipeline2.add_node(component=embedding_retriever, name="Retriever", inputs=["Query"])
embedding_querying_pipeline2.add_node(component=transformers_reader_albertv2, name="Reader", inputs=["Retriever"])


INFO - haystack.modeling.utils -  Using devices: CUDA:0 - Number of GPUs: 1


## DensePassageRetriever and FARMReader

In [19]:
from haystack.document_stores import FAISSDocumentStore
from haystack.nodes import DensePassageRetriever

#dpr_document_store = FAISSDocumentStore(similarity="dot_product")

dpr_retriever = DensePassageRetriever(
    document_store=document_store,
    query_embedding_model="facebook/dpr-question_encoder-single-nq-base",
    passage_embedding_model="facebook/dpr-ctx_encoder-single-nq-base"
)

farm_reader_albertv2 = FARMReader(model_name_or_path="mfeb/albert-xxlarge-v2-squad2", use_gpu=True)

dense_querying_pipeline = Pipeline()
dense_querying_pipeline.add_node(component=dpr_retriever, name="Retriever", inputs=["Query"])
dense_querying_pipeline.add_node(component=farm_reader_albertv2, name="Reader", inputs=["Retriever"])


INFO - haystack.modeling.utils -  Using devices: CUDA:0 - Number of GPUs: 1
INFO - haystack.modeling.model.language_model -  Auto-detected model language: english
The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'DPRQuestionEncoderTokenizer'. 
The class this function is called from is 'DPRContextEncoderTokenizerFast'.
INFO - haystack.modeling.model.language_model -  Auto-detected model language: english
INFO - haystack.modeling.utils -  Using devices: CUDA:0 - Number of GPUs: 1
INFO - haystack.modeling.utils -  Using devices: CUDA:0 - Number of GPUs: 1
INFO - haystack.modeling.model.language_model -   * LOADING MODEL: 'mfeb/albert-xxlarge-v2-squad2' (Albert)
INFO - haystack.modeling.model.language_model -  Auto-detected model language: english
INFO - haystack.modeling.model.language_model -  Loaded 'mfeb/albert-xxlarge-v2-squad

## Asking a Question


In [33]:
from pprint import pprint
def get_answer(querying_pipeline, query):
    prediction = querying_pipeline.run(
    query=query,
    params={
        "Retriever": {"top_k": 5},
        "Reader": {"top_k": 1,"debug": True}
    })
    
    return prediction["answers"][0].answer
    
    
    
    

In [21]:
top_10_questions = pd.read_csv("top100questions.csv").iloc[:10].question.tolist()

top_10_questions

['How do I check if PyTorch is using the GPU?\n',
 'How do I save a trained model in PyTorch?\n',
 'What does .view() do in PyTorch?\n',
 'Why do we need to call zero_grad() in PyTorch?\n',
 'How do I print the model summary in PyTorch?\n',
 'How do I initialize weights in PyTorch?\n',
 'What does model.eval() do in pytorch?\n',
 "What's the difference between reshape and view in pytorch?\n",
 'What does model.train() do in PyTorch?\n',
 'What does .contiguous() do in PyTorch?\n']

In [22]:
## bm25_querying_pipeline - BM25Retriever and FarmReader roberta

bm25_roberta = []
for query in top_10_questions:
    answer = get_answer(bm25_querying_pipeline, query)
    
    print("Query: ", query)
    print("Answer: ", answer)
    bm25_roberta.append(answer)
    print("\n\n\n")

/opt/conda/envs/pytorch/lib/python3.9/site-packages/elasticsearch/connection/base.py:200: ElasticsearchWarning: Elasticsearch built-in security features are not enabled. Without authentication, your cluster could be accessible to anyone. See https://www.elastic.co/guide/en/elasticsearch/reference/7.17/security-minimal-setup.html to enable security.
  warnings.warn(message, category=ElasticsearchWarning)
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that wo

Inferencing Samples:   0%|          | 0/2 [00:00<?, ? Batches/s]

INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.


Query:  How do I check if PyTorch is using the GPU?

Answer:  identify the model of your graphics card






Inferencing Samples:   0%|          | 0/2 [00:00<?, ? Batches/s]

...

Inferencing Samples:   0%|          | 0/2 [00:00<?, ? Batches/s]

INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.


Query:  What does model.train() do in PyTorch?

Answer:  run multiple times and print output






Inferencing Samples:   0%|          | 0/2 [00:00<?, ? Batches/s]

Query:  What does .contiguous() do in PyTorch?

Answer:  to convert non-contiguous tensors to contiguous tensors






In [24]:
## embedding_querying_pipeline - EmbeddingRetriever using sentence-transformers and FarmReader albert xxlargev1

embedding_albertxxlv1 = []
for query in top_10_questions:
    answer = get_answer(embedding_querying_pipeline, query)
    
    print("Query: ", query)
    print("Answer: ", answer)
    embedding_albertxxlv1.append(answer)
    print("\n\n\n")

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.


Inferencing Samples:   0%|          | 0/2 [00:00<?, ? Batches/s]

Query:  How do I check if PyTorch is using the GPU?

Answer:  torch.cuda.is_available()






Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Query:  What does model.train() do in PyTorch?

Answer:  train(model, batch)






Batches:   0%|          | 0/1 [00:00<?, ?it/s]

INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.


Inferencing Samples:   0%|          | 0/2 [00:00<?, ? Batches/s]

Query:  What does .contiguous() do in PyTorch?

Answer:  a no-op






In [25]:
## embedding_querying_pipeline1 - EmbeddingRetriever using sentence-transformers and FarmReader albert xxlargev2

embedding_albertxxlv2 = []
for query in top_10_questions:
    answer = get_answer(embedding_querying_pipeline1, query)
    
    print("Query: ", query)
    print("Answer: ", answer)
    embedding_albertxxlv2.append(answer)
    print("\n\n\n")

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.


Inferencing Samples:   0%|          | 0/2 [00:00<?, ? Batches/s]

Query:  How do I check if PyTorch is using the GPU?

Answer:  torch.cuda.is_available()






Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Query:  What does model.train() do in PyTorch?

Answer:  train(model, batch)






Batches:   0%|          | 0/1 [00:00<?, ?it/s]

INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.


Inferencing Samples:   0%|          | 0/2 [00:00<?, ? Batches/s]

Query:  What does .contiguous() do in PyTorch?

Answer:  tensor.permute(2,0,1,3).contiguous()






In [26]:
## embedding_querying_pipeline2 - EmbeddingRetriever using sentence-transformers and TransformersReader albert xxlargev2

embedding_transformersReader = []
for query in top_10_questions:
    answer = get_answer(embedding_querying_pipeline2, query)
    
    print("Query: ", query)
    print("Answer: ", answer)
    embedding_transformersReader.append(answer)
    print("\n\n\n")

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.


Query:  How do I check if PyTorch is using the GPU?

Answer:   torch.cuda.is_available()






Batches:   0%|          | 0/1 [00:00<?, ?it/s]

INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.


...

INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.


Query:  What does model.train() do in PyTorch?

Answer:  
train(model, batch)






Batches:   0%|          | 0/1 [00:00<?, ?it/s]

INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.


Query:  What does .contiguous() do in PyTorch?

Answer:   essentially a no-op,






In [27]:
## dense_querying_pipeline - DensePassageRetriever and FarmReader

dense_retriever = []
for query in top_10_questions:
    answer = get_answer(dense_querying_pipeline, query)
    
    print("Query: ", query)
    print("Answer: ", answer)
    dense_retriever.append(answer)
    print("\n\n\n")

INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.


Inferencing Samples:   0%|          | 0/2 [00:00<?, ? Batches/s]

INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.


Query:  How do I check if PyTorch is using the GPU?

Answer:  compare

import numpy as np
a = np.ones(5)
b = a

followed by either

np.add(a, 1, out=a)
print(b)

or

a = a + 1
print(b)






Inferencing Samples:   0%|          | 0/18 [00:00<?, ? Batches/s]

...

Inferencing Samples:   0%|          | 0/2 [00:00<?, ? Batches/s]

INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.
INFO - haystack.schema -  Setting the ID manually. This might cause a mismatch with the ID that would be generated from the document content and id_hash_keys value.


Query:  What does model.train() do in PyTorch?

Answer:  pytorch already has built in pruning related package






Inferencing Samples:   0%|          | 0/3 [00:00<?, ? Batches/s]

Query:  What does .contiguous() do in PyTorch?

Answer:  variable(torch.from_numpy(nopeak_mask)






In [28]:
data = {'questions':top_10_questions, 'bm25_roberta':bm25_roberta, 'embedding_albertxxlv1':embedding_albertxxlv1, 'embedding_albertxxlv2':embedding_albertxxlv2,'embedding_transformersReader_v2':embedding_transformersReader,'dense_retriever':dense_retriever}

In [27]:
df1 = pd.DataFrame(data)
df1

questions  \
0                 How do I check if PyTorch is using the GPU?\n   
1                   How do I save a trained model in PyTorch?\n   
2                            What does .view() do in PyTorch?\n   
3              Why do we need to call zero_grad() in PyTorch?\n   
4                How do I print the model summary in PyTorch?\n   
5                     How do I initialize weights in PyTorch?\n   
6                       What does model.eval() do in pytorch?\n   
7  What's the difference between reshape and view in pytorch?\n   
8                      What does model.train() do in PyTorch?\n   
9                      What does .contiguous() do in PyTorch?\n   

                                                       bm25_roberta  \
0                          identify the model of your graphics card   
1                                                  however you want   
2  expects the new shape to be provided by individual int arguments   
3    when we want to &quot;conserve&quot; ram with massive datasets   
4                                                      forward_pass   
5                                                    adjust\nnewval   
6                                          fix the parameters of bn   
7                                             two different methods   
8                               run multiple times and print output   
9              convert non-contiguous tensors to contiguous tensors   

                                                             embedding_albertxxlv1  \
0                                                        torch.cuda.is_available()   
1  you can directly save the model itself, or you can save a dictionary that in...   
2   creates a view with different dimensions of the storage associated with tensor   
3                                                        reduce memory consumption   
4                                                           #print(cost(x,y,beta))   
5                          self.weight = torch.nn.linear(in_features, out_featues)   
6                                                         fix the parameters of bn   
7                                                               explicit exception   
8                                                              train(model, batch)   
9                                                                          a no-op   

                                                             embedding_albertxxlv2  \
0                                                        torch.cuda.is_available()   
1  checkpoint = {'state_dict': model.state_dict(),'optimizer' :optimizer.state_...   
2                                                         reshapes the tensor to a   
3                           you are passing the map_location to the wrong function   
4                                                  summary(self.model, (1, 34, 8))   
5                                         from the weights of the pretrained model   
6                                                         fix the parameters of bn   
7                                     .contiguous().view(shape) will create a copy   
8                                                              train(model, batch)   
9                                             tensor.permute(2,0,1,3).contiguous()   

                              embedding_transformersReader_v2  \
0                                   torch.cuda.is_available()   
1  \nis it possible to save a file from test_step() function?   
2    reshapes the tensor to a different but compatible shape.   
3                                 too many indices for array"   
4                             summary(self.model, (1, 34, 8))   
5                                                   randomly:   
6                                   fix the parameters of bn,   
7                    z0 is a new view of x, but z1 is a copy:   
8                                       \ntrain(model, 

In [28]:
df1.to_csv('haystack_comparison.csv')